# Notebook to create the network

In [6]:
import requests
import json
import re
import networkx as nx
import numpy as np
import os
from io import StringIO
import pandas as pd
import nltk
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
nltk.download('stopwords')
from collections import Counter
import nltk

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Maria\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


## 1. Fetch list of countries

In [7]:
baseurl = "https://en.wikipedia.org/w/api.php?"
action = "action=query"
title = "titles=Member_states_of_the_United_Nations"
content = "prop=revisions&rvprop=content"
dataformat ="format=json"

query = "{}{}&{}&{}&{}".format(baseurl, action, content, title, dataformat)
print(query)

https://en.wikipedia.org/w/api.php?action=query&prop=revisions&rvprop=content&titles=Member_states_of_the_United_Nations&format=json


Fetch raw data

In [8]:
headers = {"User-Agent" : "MyWikipediaClient/1.0 (example@example.com)"} # just use this dict as-is.
wikiresponse = requests.get(query, headers=headers)
wikidata = wikiresponse.text
dict_data=json.loads(wikidata)

In [9]:
raw_data=dict_data['query']['pages']['31969']['revisions'][0]['*']
raw_data

'{{Short description|none}}\n{{For|the League of Nations|Member states of the League of Nations}}\n{{Featured list}}\n{{pp-pc|small=yes}}\n{{Use dmy dates|date=February 2025}}\n{{Use Oxford spelling|date = February 2025}}\n\n[[File:United Nations (Member States and Territories).svg|thumb|\n{{legend|#009edb|193 United Nations member states}}\n{{legend|#9edb00|2 [[United Nations General Assembly observers#Current non-member observers|UN General Assembly observer states]] (the [[Holy See]]{{efn|The [[sovereignty|sovereign entity]] with [[state (polity)|statehood]] over the territory of the [[Vatican City|Vatican City State]].}} and [[Palestine]])}}\n{{legend|#db9e00|2 non-member states (the [[Cook Islands]] and [[Niue]])<ref>{{Cite web|url = https://www.un.org/en/development/desa/population/publications/pdf/policy/WPP2013/Chapters/a_Preface.pdf |title = UN: "Data for 197 countries: all 193 member states, two observer states (the Holy See and Palestine), and two non-member states (Cook Isl

Get countries using flag because they all appear as one of these: {flag|country}, {flagdeco|country}, {flagcountry|country}

This list of countries is a list of strings that have:
- capital letters
- there are white spaces (substituir later por underscore)

This list doesnt work to access wikipedia.

In [10]:
countries = re.findall(r"\{flag(?:deco|country)?\|([^|}]+)", raw_data)
no_countries = len(countries)
print("Number of countries:", no_countries)

Number of countries: 193


## 2. Fetch wikipages of countries

Countries doesnt work in wikipedia

Countries_clean works in wikipedia

In [11]:
countries = [re.sub(r"\s*\(.*?\)", "", c).strip() for c in countries]
countries_clean=[]
for c in countries:
    if c=="Bahamas":
        c="The_Bahamas"
    if c=="Cabo Verde":
        c="Cape_Verde"
    if c=="Côte d'Ivoire":
        c="Ivory_Coast"
    if c=="Czechia":
        c="Czech_Republic"
    if c=="Guinea Bissau":
        c="Guinea-Bissau"
    if c=="Lao People's Democratic Republic":
        c="Laos"
    if c=="Republic of Korea":
        c="South_Korea"
    if c=="Republic of Moldova":
        c="Moldova"
    if c=="Russian Federation":
        c="Russia"
    if c=="Syrian Arab Republic":
        c="Syria"
    if c=="Sao Tome and Principe":
        c="São_Tomé_and_Príncipe"
    if c=="United Kingdom of Great Britain and Northern Ireland":
        c="United_Kingdom"
    if c=="United Republic of Tanzania":
        c="Tanzania"
    if c=="Türkiye":
        c="Turkey"
    if c=="United States of America":
        c="United_States"
    new_c = c.replace(" ", "_")
    countries_clean.append(new_c)

In [12]:
len(countries_clean) == len(countries)

True

Vai buscar a secção History de cada pais, acedendo a wikipedia, mas nao tem o texto das referencias no meio

In [ ]:
# baseurl = "https://en.wikipedia.org/w/api.php?"
# headers = {"User-Agent" : "MyWikipediaClient/1.0 (example@example.com)"} # just use this dict as-is.

# folder_name = "countries_pages"
# os.makedirs(folder_name, exist_ok=True)

# for c in countries_clean:

#     print(c)

#     # get index for history section
#     params_sections = {"action": "parse", "page": c, "prop": "sections", "format": "json"}
#     r = requests.get(baseurl, params=params_sections, headers=headers)
#     sections_data = r.json()
#     for s in sections_data["parse"]["sections"]:
#     #print(s["index"], s["line"])
#         if s["line"] == "History":
#             history_index = s["index"]
#             break

#     # get text of history section
#     params_text = {"action": "parse", "page": c, "prop": "wikitext", "section": history_index, "format": "json"}
#     r2 = requests.get(baseurl, params=params_text, headers=headers)
#     r2_text = r2.text
#     history_data=json.loads(r2_text)
#     print(history_data)
#     history_text=history_data["parse"]["wikitext"]["*"]
#     clean_text = re.sub(r"<ref.*?>.*?</ref>", "", history_text, flags=re.DOTALL)

#     file_path = os.path.join(folder_name, c+".txt")
#     with open(file_path, "w", encoding="utf-8") as f:
#         f.write(clean_text)

Afghanistan
{'parse': {'title': 'Afghanistan', 'pageid': 737, 'wikitext': {'*': '==History==\n{{Main|History of Afghanistan}}\n\n===Prehistory and antiquity===\n{{Main|Ancient history of Afghanistan}}\n{{See also|Hindu and Buddhist heritage of Afghanistan}}\n[[File:Nomads in Badghis Province.jpg|thumb|left|Tents of Afghan [[nomad]]s in the northern [[Badghis Province]]. Early peasant farming villages came into existence about 7,000 years ago.]]\n\nExcavations of prehistoric sites suggest that humans were living in what is now Afghanistan at least 50,000 years ago, and that farming communities in the area were among the earliest in the world. An important site of early historical activities, many believe that Afghanistan compares to [[Egypt]] in the historical value of its archaeological sites.<ref name="JFS">{{cite encyclopedia|url=http://encarta.msn.com/text_761569370___42/Afghanistan.html |title=Afghanistan&nbsp;– John Ford Shroder, University of Nebraska |publisher=Encarta |access-d

## 3. Create network

Por para encontrar todos os paises, nao so os que tem link

In [13]:
folder_name = "countries_pages"
all_items = os.listdir(folder_name)

len(all_items) == no_countries

True

In [14]:
G = nx.DiGraph()

for filename in all_items:

    #ir buscar texto deste file
    country_file_path = os.path.join(folder_name, filename)
    with open(country_file_path, "r", encoding="utf-8") as f:
        country_text = f.read()

    clean_text = re.sub(r"<ref.*?>.*?</ref>", "", country_text, flags=re.DOTALL)

    #get name of node, filename é str com .txt
    country=filename.split('.')[0]
    G.add_node(country)

    mentioned_countries = set()
    for other_country in countries_clean:
        new_other = other_country.replace("_", " ")
        if other_country == country:
            continue  # skip self
        # search anywhere in text, case-insensitive, word boundaries
        if re.search(rf"\b{re.escape(new_other)}\b", clean_text, flags=re.IGNORECASE) and other_country!=country and other_country not in mentioned_countries:
            mentioned_countries.add(other_country)
            G.add_edge(country, other_country)

In [15]:
print(G.number_of_nodes())
print(G.number_of_edges())

193
1857


In [16]:
source = "Denmark"  # the node you want to inspect

# returns an iterator of nodes that 'France' points to
outgoing_nodes = list(G.successors(source))

print(f"Nodes that {source} points to:")
for node in outgoing_nodes:
    print(" -", node)

Nodes that Denmark points to:
 - Canada
 - Estonia
 - France
 - Germany
 - Ghana
 - Iceland
 - India
 - Ireland
 - Norway
 - Russia
 - Sri_Lanka
 - Sweden
 - United_Kingdom


## 4. Sentiment score

labmt word list

In [17]:
# Based on the LabMT word list, 
# write a function that calculates sentiment given a list of tokens 
# (the tokens should be lower case, etc).

# Skip the header lines and load the word list into a DataFrame
with open("labmt_wordlist.txt", "r") as f:
    word_list = f.readlines()
    
# Join the lines and skip the first 4 lines (metadata + header)
data_str = "".join(word_list[3:])
labmt_df = pd.read_csv(StringIO(data_str), sep="\t")

# Create a dictionary for quick word → happiness lookup
labmt_dict = dict(zip(labmt_df["word"], labmt_df["happiness_average"]))

function that gives sentiment score

In [18]:
def calculate_sentiment(tokens, labmt_dict, stop_low=4.0, stop_high=6.0):
    scores = 0
    no_tokens = 0
    for token in tokens:
        score = labmt_dict.get(token)
        if score is not None:
            no_tokens+=1
            scores+=score
    if no_tokens==0:
        return
    avg=scores/no_tokens
    return avg

In [23]:
lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words("english"))


###### TEM DE SER UNDIRECTED???????????????
for node in G.nodes():

    # open artist file
    folder_path="countries_pages"
    filename = node + ".txt" 
    file_path = os.path.join(folder_path, filename)
    with open(file_path, "r", encoding="utf-8") as f:
        node_text = f.read()
    
    wiki_terms = {
    'cite', 'ref', '/ref', 'category', 'infobox', 'stub', 'short', 'description', 'template',
    'file', 'image', 'external', 'links', 'references', 'see', 'also', 'edit', 'wikidata',
    'article', 'band', 'album', 'name', 'page', 'list', 'track', 'single', 'released', 'chart',
    'music', 'label', 'record', 'records', 'artist', 'group', 'song', 'songs', 'year', 'years',
    'date', 'title', 'awards', 'award', 'official', 'website', 'link', 'bio', 'history', 'http'}
    
    tokens = nltk.word_tokenize(node_text)
    tokens = [t.lower() for t in tokens if t.isalpha() and t.lower() not in stop_words]
    tokens=[t for t in tokens if t not in wiki_terms]
    tokens = [lemmatizer.lemmatize(t) for t in tokens]
    counter = Counter(tokens)
    counter = Counter({word: count for word, count in counter.items() if count >= 5})
    
    node_clean_text=counter

    #print(node)
    sentiment=calculate_sentiment(node_clean_text,labmt_dict)

    G.nodes[node]["sentiment"] = sentiment

In [24]:
G.nodes(data=True)

NodeDataView({'Afghanistan': {'sentiment': 5.364174757281554}, 'China': {'sentiment': 5.315909090909089}, 'Egypt': {'sentiment': 5.489387755102041}, 'France': {'sentiment': 5.458214285714285}, 'India': {'sentiment': 6.42}, 'Iran': {'sentiment': 5.045833333333331}, 'Italy': {'sentiment': 5.595522388059701}, 'Pakistan': {'sentiment': 5.616666666666666}, 'Qatar': {'sentiment': 5.323478260869564}, 'Russia': {'sentiment': 5.378333333333334}, 'United_Kingdom': {'sentiment': 5.959615384615383}, 'United_States': {'sentiment': 5.696216216216217}, 'Uzbekistan': {'sentiment': 5.4575000000000005}, 'Albania': {'sentiment': 5.5307407407407405}, 'Bosnia_and_Herzegovina': {'sentiment': 5.38216216216216}, 'Bulgaria': {'sentiment': 5.3525}, 'Germany': {'sentiment': 5.464523809523808}, 'Greece': {'sentiment': 5.446666666666666}, 'Ireland': {'sentiment': 5.484050632911392}, 'Montenegro': {'sentiment': 5.408936170212767}, 'Serbia': {'sentiment': 5.455074626865672}, 'Spain': {'sentiment': 5.621098901098901}

## 4. Add attributes from dataset